In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/titanic/train.csv
/kaggle/input/titanic/test.csv
/kaggle/input/titanic/gender_submission.csv


In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import pandas_profiling as pp
import warnings
warnings.filterwarnings('ignore')

/opt/conda/lib/python3.10/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.23.5
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"
/opt/conda/lib/python3.10/site-packages/numba/core/decorators.py:262: NumbaDeprecationWarning: numba.generated_jit is deprecated. Please see the documentation at: https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-generated-jit for more information and advice on a suitable replacement.
  warnings.warn(msg, NumbaDeprecationWarning)
/opt/conda/lib/python3.10/site-packages/visions/backends/shared/nan_handling.py:51: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-o

In [3]:
train_data=pd.read_csv('/kaggle/input/titanic/train.csv')
train_data.head()

PassengerId  Survived  Pclass  \
0            1         0       3   
1            2         1       1   
2            3         1       3   
3            4         1       1   
4            5         0       3   

                                                Name     Sex   Age  SibSp  \
0                            Braund, Mr. Owen Harris    male  22.0      1   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0      1   
2                             Heikkinen, Miss. Laina  female  26.0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0      1   
4                           Allen, Mr. William Henry    male  35.0      0   

   Parch            Ticket     Fare Cabin Embarked  
0      0         A/5 21171   7.2500   NaN        S  
1      0          PC 17599  71.2833   C85        C  
2      0  STON/O2. 3101282   7.9250   NaN        S  
3      0            113803  53.1000  C123        S  
4      0            373450   8.0500   NaN        S

In [4]:
test_data=pd.read_csv('/kaggle/input/titanic/test.csv')
test_data.head()

PassengerId  Pclass                                          Name     Sex  \
0          892       3                              Kelly, Mr. James    male   
1          893       3              Wilkes, Mrs. James (Ellen Needs)  female   
2          894       2                     Myles, Mr. Thomas Francis    male   
3          895       3                              Wirz, Mr. Albert    male   
4          896       3  Hirvonen, Mrs. Alexander (Helga E Lindqvist)  female   

    Age  SibSp  Parch   Ticket     Fare Cabin Embarked  
0  34.5      0      0   330911   7.8292   NaN        Q  
1  47.0      1      0   363272   7.0000   NaN        S  
2  62.0      0      0   240276   9.6875   NaN        Q  
3  27.0      0      0   315154   8.6625   NaN        S  
4  22.0      1      1  3101298  12.2875   NaN        S

In [5]:
pp.ProfileReport(train_data, title = 'Profiling report of "Train" set', html = {'style':{'full_width': True}})

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [6]:
pp.ProfileReport(test_data, title = 'Profiling report of "Test" set', html = {'style':{'full_width': True}})

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [7]:
common_value = 'S'
train_data["Embarked"] = train_data["Embarked"].fillna(common_value)

In [8]:
test_data = test_data.fillna(test_data['Fare'].mean())

In [9]:
data = [train_data, test_data]

for dataset in data:
    mean = train_data["Age"].mean()
    std = test_data["Age"].std()
    is_null = dataset["Age"].isnull().sum()
    # compute random numbers between the mean, std and is_null
    rand_age = np.random.randint(mean - std, mean + std, size = is_null)
    # fill NaN values in Age column with random values generated
    age_slice = dataset["Age"].copy()
    age_slice[np.isnan(age_slice)] = rand_age
    dataset["Age"] = age_slice
    dataset["Age"] = train_data["Age"].astype(int)
train_data["Age"].isnull().sum()

0

In [10]:
train_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 891 entries, 0 to 890
Data columns (total 12 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   PassengerId  891 non-null    int64  
 1   Survived     891 non-null    int64  
 2   Pclass       891 non-null    int64  
 3   Name         891 non-null    object 
 4   Sex          891 non-null    object 
 5   Age          891 non-null    int64  
 6   SibSp        891 non-null    int64  
 7   Parch        891 non-null    int64  
 8   Ticket       891 non-null    object 
 9   Fare         891 non-null    float64
 10  Cabin        204 non-null    object 
 11  Embarked     891 non-null    object 
dtypes: float64(1), int64(6), object(5)
memory usage: 83.7+ KB


In [11]:
test_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 418 entries, 0 to 417
Data columns (total 11 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   PassengerId  418 non-null    int64  
 1   Pclass       418 non-null    int64  
 2   Name         418 non-null    object 
 3   Sex          418 non-null    object 
 4   Age          418 non-null    int64  
 5   SibSp        418 non-null    int64  
 6   Parch        418 non-null    int64  
 7   Ticket       418 non-null    object 
 8   Fare         418 non-null    float64
 9   Cabin        418 non-null    object 
 10  Embarked     418 non-null    object 
dtypes: float64(1), int64(5), object(5)
memory usage: 36.0+ KB


In [12]:
from sklearn.preprocessing import LabelEncoder
le = LabelEncoder()
train_data["Sex"]= le.fit_transform(train_data["Sex"])
print(train_data["Sex"])

0      1
1      0
2      0
3      0
4      1
      ..
886    1
887    0
888    0
889    1
890    1
Name: Sex, Length: 891, dtype: int64


In [13]:
test_data["Sex"]= le.fit_transform(test_data["Sex"])
print(test_data["Sex"])

0      1
1      0
2      1
3      1
4      0
      ..
413    1
414    0
415    1
416    1
417    1
Name: Sex, Length: 418, dtype: int64


In [14]:
train_data["Embarked"]= le.fit_transform(train_data["Embarked"])
print(train_data["Embarked"])

0      2
1      0
2      2
3      2
4      2
      ..
886    2
887    2
888    2
889    0
890    1
Name: Embarked, Length: 891, dtype: int64


In [15]:
test_data["Embarked"]= le.fit_transform(test_data["Embarked"])
print(test_data["Embarked"])

0      1
1      2
2      1
3      2
4      2
      ..
413    2
414    0
415    2
416    2
417    0
Name: Embarked, Length: 418, dtype: int64


In [16]:
train_data.head()

PassengerId  Survived  Pclass  \
0            1         0       3   
1            2         1       1   
2            3         1       3   
3            4         1       1   
4            5         0       3   

                                                Name  Sex  Age  SibSp  Parch  \
0                            Braund, Mr. Owen Harris    1   22      1      0   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...    0   38      1      0   
2                             Heikkinen, Miss. Laina    0   26      0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)    0   35      1      0   
4                           Allen, Mr. William Henry    1   35      0      0   

             Ticket     Fare Cabin  Embarked  
0         A/5 21171   7.2500   NaN         2  
1          PC 17599  71.2833   C85         0  
2  STON/O2. 3101282   7.9250   NaN         2  
3            113803  53.1000  C123         2  
4            373450   8.0500   NaN         2

In [17]:
test_data.head()

PassengerId  Pclass                                          Name  Sex  \
0          892       3                              Kelly, Mr. James    1   
1          893       3              Wilkes, Mrs. James (Ellen Needs)    0   
2          894       2                     Myles, Mr. Thomas Francis    1   
3          895       3                              Wirz, Mr. Albert    1   
4          896       3  Hirvonen, Mrs. Alexander (Helga E Lindqvist)    0   

   Age  SibSp  Parch   Ticket     Fare      Cabin  Embarked  
0   22      0      0   330911   7.8292  35.627188         1  
1   38      1      0   363272   7.0000  35.627188         2  
2   26      0      0   240276   9.6875  35.627188         1  
3   35      0      0   315154   8.6625  35.627188         2  
4   35      1      1  3101298  12.2875  35.627188         2

In [18]:
train_data=train_data.drop("Name",axis=1)
train_data=train_data.drop("Ticket",axis=1)
train_data=train_data.drop("Cabin",axis=1)
test_data=test_data.drop("Name",axis=1)
test_data=test_data.drop("Ticket",axis=1)
test_data=test_data.drop("Cabin",axis=1)

In [19]:
train_data.head()

PassengerId  Survived  Pclass  Sex  Age  SibSp  Parch     Fare  Embarked
0            1         0       3    1   22      1      0   7.2500         2
1            2         1       1    0   38      1      0  71.2833         0
2            3         1       3    0   26      0      0   7.9250         2
3            4         1       1    0   35      1      0  53.1000         2
4            5         0       3    1   35      0      0   8.0500         2

In [20]:
test_data.head()

PassengerId  Pclass  Sex  Age  SibSp  Parch     Fare  Embarked
0          892       3    1   22      0      0   7.8292         1
1          893       3    0   38      1      0   7.0000         2
2          894       2    1   26      0      0   9.6875         1
3          895       3    1   35      0      0   8.6625         2
4          896       3    0   35      1      1  12.2875         2

In [21]:
X_tr = train_data.drop("Survived", axis=1)
Y_tr = train_data["Survived"]
X_test  = test_data

In [22]:
X_test.head()

PassengerId  Pclass  Sex  Age  SibSp  Parch     Fare  Embarked
0          892       3    1   22      0      0   7.8292         1
1          893       3    0   38      1      0   7.0000         2
2          894       2    1   26      0      0   9.6875         1
3          895       3    1   35      0      0   8.6625         2
4          896       3    0   35      1      1  12.2875         2

In [23]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()
X_tr= sc.fit_transform(X_tr)
X_test = sc.transform(X_test)

In [24]:
print(X_tr)

[[-1.73010796  0.82737724  0.73769513 ... -0.47367361 -0.50244517
   0.58595414]
 [-1.72622007 -1.56610693 -1.35557354 ... -0.47367361  0.78684529
  -1.9423032 ]
 [-1.72233219  0.82737724 -1.35557354 ... -0.47367361 -0.48885426
   0.58595414]
 ...
 [ 1.72233219  0.82737724 -1.35557354 ...  2.00893337 -0.17626324
   0.58595414]
 [ 1.72622007 -1.56610693  0.73769513 ... -0.47367361 -0.04438104
  -1.9423032 ]
 [ 1.73010796  0.82737724  0.73769513 ... -0.47367361 -0.49237783
  -0.67817453]]


In [25]:
print(Y_tr)

0      0
1      1
2      1
3      1
4      0
      ..
886    0
887    1
888    0
889    1
890    0
Name: Survived, Length: 891, dtype: int64


In [26]:
from sklearn.linear_model import LogisticRegression
classifier = LogisticRegression(random_state=0)
classifier.fit(X_tr,Y_tr)

LogisticRegression(random_state=0)

In [27]:
from sklearn.metrics import accuracy_score
predict = classifier.predict(X_tr)
score = accuracy_score(Y_tr,predict)
print(score)

0.797979797979798
